# Data enrichment

### <u>Content:<u>

[1) Load data sets

[2) Add week day and month to reservation data
    
[3) Estimate part of the Swiss population that is on holiday for any given date
    
[4) Add coordinates for start and destination 

[5) Get weather data
    
[6) Get capacity data for trains in 2020 according to the expected train formation


In [1]:
#Import packages
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pylab import rcParams
import seaborn as sns
import scipy
from scipy.spatial.distance import cdist
import dateutil
import math
import meteomatics.api as api
import datetime as dt
%matplotlib inline
rcParams['figure.figsize']=10,8

#### 1) Load data

In [ ]:
#read the reservation data 
df = pd.read_csv('data_raw/reservation_data_2019-2021_incl_capacity.csv', 
                 parse_dates=["date"], date_parser=lambda x: pd.to_datetime(x, format="%Y-%m-%d %H:%M:%S"))         
        
print('reservations: ')
display(df.tail(1))

df

# read holiday data
df_schulferien = pd.read_csv('data_preprocessed/Schulferien.csv', dtype={"canton": "string", "population": "int32"})
df_schulferien['start'] = pd.to_datetime(df_schulferien['holidays_start'])
df_schulferien['end'] = pd.to_datetime(df_schulferien['holidays_end'])
df_schulferien = df_schulferien.drop(columns=["holidays_start", "holidays_end"])

print('schulferien: ')
display(df_schulferien.tail(1))

# train station coordinates data
df_coordinates = pd.read_csv('data_preprocessed/dienststellen.csv')
df_coordinates = df_coordinates[["abk_bahnhof", "lat", "lon"]]
df_coordinates = df_coordinates[df_coordinates['abk_bahnhof'].notna()]
display(df_coordinates.tail(1))

# weather data
df_weather = pd.read_csv("data_preprocessed/weather.csv")
#                        parse_dates=["validdate"], date_parser=lambda x: pd.to_datetime(x, format="%Y-%m-%d%T%H:%M:%S%Z"))         

#df_weather['date'] = df_weather['validdate'].apply(dateutil.parser.parse)
display(df_weather.tail(1))

# jahresformation
df_jahresformation = pd.read_csv("data_preprocessed/jahresformation.csv", dtype={"Block Bezeichnung": "string"})
display(df_jahresformation.tail(1))
df_jahresformation.dtypes

# kapazität
df_kapazität = pd.read_csv("data_preprocessed/rollmaterial-matching.csv")
display(df_kapazität.tail(1))


#### 2) Week day <a name="stat"></a>

- Add a feature for weekday: 'weekday' and 'month'

In [102]:
df['weekday'] = df['date'].dt.dayofweek
df['month'] = df['date'].dt.month

#### 3) Holidays <a name="stat"></a>
- Add a feature for number of people in holiday canton: n_holiday

In [8]:
# for each date, get the number of people in Switzerland who 
# are either on school holiday or national holiday..
def get_holiday_people(date):
    filtered_holidays = df_schulferien[(df_schulferien['start']<=date)&(df_schulferien['end']>=date)]
    is_national_holiday = (filtered_holidays["canton"]=="national").sum()
    if is_national_holiday:
        people = 7917100
    elif not(filtered_holidays.empty):
        filtered_holidays = filtered_holidays[filtered_holidays["canton"]!="national"]
        people = sum(filtered_holidays["population"])
    else: people=0
    return people

In [ ]:
# filter df, only 2021 data
# df=df[df['date']>='2021-01-01']
df['holiday_people'] = df.apply(lambda row : get_holiday_people(row['date']), axis = 1)


#### 4) Coordinates <a name="hr"></a>

In [103]:
# full join for start train station 
df = pd.merge(df, df_coordinates, left_on='bp_from', right_on='abk_bahnhof')
df = df.drop(columns=['abk_bahnhof']).rename(columns={"lat": "lat_from", "lon": "lon_from"})

# full join for destination
df = pd.merge(df, df_coordinates, left_on='bp_to', right_on='abk_bahnhof')
df = df.drop(columns=['abk_bahnhof']).rename(columns={"lat": "lat_to", "lon": "lon_to"})
display(df.head(2))

Unnamed: 0  res_id               res_dt       date  train_nr  line  \
0           0       0  2019-03-29 00:00:00 2019-04-01       510  IC 5   
1         283     290  2019-04-06 00:00:00 2019-04-06      1528  IC 5   

   reserved  capacity bp_from bp_to  ...             arr_soll res_delta_ist  \
0         1       NaN     ZUE    NE  ...  2019-04-01 08:32:00      284667.0   
1         1       NaN     ZUE    NE  ...  2019-04-06 18:01:00       59422.0   

  res_delta_soll res_delta_valid  weekday  month   lat_from  lon_from  \
0         284634           False        0      4  47.378177  8.540212   
1          59418           False        5      4  47.378177  8.540212   

      lat_to    lon_to  
0  46.996727  6.935702  
1  46.996727  6.935702  

[2 rows x 23 columns]

#### 5) Weather <a name="corr"></a>

In [ ]:
# weather data
df_weather = pd.read_csv("data_preprocessed/weather.csv")
    parse_dates=["validdate"], date_parser=lambda x: pd.to_datetime(x, format="%Y-%m-%d%T%H:%M:%S%Z"))         

#df_weather['date'] = df_weather['validdate'].apply(dateutil.parser.parse)
display(df_weather.tail(1))

In [ ]:
##import meteo data 
username = 'can-guru_otth'
password = 'eyk47W6ATq'
coordinates = [(47.378177, 8.540212)]
#model =     'mix'

startdate = dt.datetime(year=2022, month=4, day=9, hour=0, minute=0, second=0)
enddate =   startdate 

parameters = ['t_2m:C','precip_24h:mm', 'leisure_biking:idx']
format = 'csv'

df = api.query_time_series(coordinates, startdate, enddate, interval, parameters, username, password, model=model)

print(df)

#### 6) Capacity <a name="corr"></a>

 - Für jede Reservation: Zugnummer im Jahresformation-Datensatz abrufen
 - Beachte: richtiges Jahr wählen, häufigste Formation
 - entsprechende Kapazität auslesen

In [104]:
#combine data from capacity table and annual formation
list_kapazitäten=df_kapazität["Block Bezeichnung in Jahresformation Fpl-2022"].tolist()
df_jahresformation = df_jahresformation[df_jahresformation["Block Bezeichnung"].isin(list_kapazitäten)]
df_jahresformation=df_jahresformation[["Block Bezeichnung", "Zug", "Beginn Fahrplanperiode"]]
df_jahresformation = pd.merge(df_jahresformation, df_kapazität, left_on='Block Bezeichnung', right_on='Block Bezeichnung in Jahresformation Fpl-2022').drop(columns=["Block Bezeichnung in Jahresformation Fpl-2022"])
df_jahresformation.tail(2)

Block Bezeichnung   Zug Beginn Fahrplanperiode  \
18204  Re460 A4(hp)2Apm Bpm 2B4 2B4(78) Bt4 GBT  2682               Fpl-2022   
18205  Re460 A4(hp)2Apm Bpm 2B4 2B4(78) Bt4 GBT  2567                    NaN   

       No. of hooks  
18204            16  
18205            16

In [105]:
median_df=df[df["capacity"].notnull()]
median=np.median(median_df['capacity'])
print('Median Kapazität', median)

Median Kapazität 12.0


In [120]:
def fill_capacity(row):
    train=row.train_nr   
    formation = df_jahresformation[df_jahresformation["Zug"]==train]
    print(len(formation))
    display(formation)
    capacity=mformation["No. of hooks"]
    return capacity

In [ ]:
# for the rows where there is no capacity included
# first try to check with the jahresformation lookup table
mask = df.capacity.isnull()
df['capacity'] = df[mask].apply(fill_capacity, axis=1)

# secondly, fill the median capacity 
df=df.fillna(value={"capacity": median})

50


Block Bezeichnung  Zug Beginn Fahrplanperiode  No. of hooks
2375  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
2574  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
2575  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
2576  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
2577  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
2753  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
2754  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
2755  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
2923  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
2924  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
3111  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
3277  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
3643  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
3644  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
3645  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
3829  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
3830  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
3831  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
3832  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4036  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4037  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4038  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4227  ICN: Bt B WRA A AD B Bt  510               Fpl-2019             6
4406  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
4407  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
4408  ICN: Bt B WRA A AD B Bt  510               FPL-2020             6
4590  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4591  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4813  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4814  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4815  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
4816  ICN: Bt B WRA A AD B Bt  510               Fpl-2021             6
5026  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5027  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5238  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5239  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5240  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5241  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5453  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5454  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5455  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5660  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5661  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5662  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5663  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5664  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5665  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5850  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5851  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6
5852  ICN: Bt B WRA A AD B Bt  510               Fpl-2022             6

50


Block Bezeichnung   Zug Beginn Fahrplanperiode  No. of hooks
2291  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
2292  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
2293  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
2294  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
2295  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
2506  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
2507  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
2508  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
2696  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
2849  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
3031  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
3229  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
3230  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
3412  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3413  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3414  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3415  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3416  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3417  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3418  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3419  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3420  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3582  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
3583  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
3584  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
3585  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
3771  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
3772  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
3973  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3974  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3975  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
3976  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
4163  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
4340  ICN: Bt B WRA A AD B Bt  1528                    NaN             6
4341  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
4342  ICN: Bt B WRA A AD B Bt  1528               Fpl-2019             6
4533  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
4534  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
4535  ICN: Bt B WRA A AD B Bt  1528               FPL-2020             6
4751  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
4752  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
4959  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
4960  ICN: Bt B WRA A AD B Bt  1528               Fpl-2021             6
5123  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5124  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5125  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5331  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5332  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5550  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6
5944  ICN: Bt B WRA A AD B Bt  1528               Fpl-2022             6

43


...

37


Block Bezeichnung  Zug Beginn Fahrplanperiode  No. of hooks
2201  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
2202  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
2203  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
2392  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
2393  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
2394  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
2933  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
3124  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3125  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3126  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3291  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
3487  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
3488  ICN: Bt B WRA A AD B Bt  516               Fpl-2019             6
3659  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3660  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3661  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3662  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
3841  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
3842  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4048  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4049  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4050  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4051  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4432  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
4433  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
4434  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
4435  ICN: Bt B WRA A AD B Bt  516               FPL-2020             6
4605  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4606  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4607  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4831  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
4832  ICN: Bt B WRA A AD B Bt  516               Fpl-2021             6
5043  ICN: Bt B WRA A AD B Bt  516               Fpl-2022             6
5044  ICN: Bt B WRA A AD B Bt  516               Fpl-2022             6
5250  ICN: Bt B WRA A AD B Bt  516               Fpl-2022             6
5466  ICN: Bt B WRA A AD B Bt  516               Fpl-2022             6
5673  ICN: Bt B WRA A AD B Bt  516               Fpl-2022             6

27


Block Bezeichnung  Zug Beginn Fahrplanperiode  No. of hooks
2406  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
2770  ICN: Bt B WRA A AD B Bt  524               Fpl-2019             6
2771  ICN: Bt B WRA A AD B Bt  524               Fpl-2019             6
2939  ICN: Bt B WRA A AD B Bt  524               Fpl-2019             6
3136  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3137  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3138  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3139  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3140  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3304  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
3305  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
3495  ICN: Bt B WRA A AD B Bt  524               Fpl-2019             6
3496  ICN: Bt B WRA A AD B Bt  524               Fpl-2019             6
3672  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
3673  ICN: Bt B WRA A AD B Bt  524               FPL-2020             6
4060  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4622  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4623  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4624  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4849  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4850  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4851  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
4852  ICN: Bt B WRA A AD B Bt  524               Fpl-2021             6
5053  ICN: Bt B WRA A AD B Bt  524               Fpl-2022             6
5479  ICN: Bt B WRA A AD B Bt  524               Fpl-2022             6
5678  ICN: Bt B WRA A AD B Bt  524               Fpl-2022             6
5679  ICN: Bt B WRA A AD B Bt  524               Fpl-2022             6

54


In [ ]:
df.head(10)